In [2]:
import sqlite3
# import os.path
import hashlib
import pandas as pd
import numpy as np

name = "disaggregator_results_pie"
name = "Matthijs"

db = './../data/daf06fb3ab69f27bd681a63311722181.db'
db = './test.db'
db = './../data/Matthijs/1cb93dd0babab36e9e5efe90a47d7824.db'


conn = sqlite3.connect(db)

df = pd.read_sql_query("SELECT * FROM loadsonly;", conn)
conn.close()# close db

df['datetime'] = pd.to_datetime(df['datetime'])
df.sort_values(by='datetime',ascending=True);


In [3]:
df['dp'] = df['demand'] - df['demand'].shift(1)
df['dp+'] = [0-x if x <=0 else 0 for x in df['dp']]
df['dp-'] = [x if x >=0 else 0 for x in df['dp']]

df['dp'] = df['demand'] - df['demand'].shift(1)
for x in range(1,len(df)):
    df.loc[x,'dp'] = df.loc[x,'demand'] -  df.loc[x-1,'demand']
    if df.loc[x,'dp'] > 0:
        df.loc[x,'dp+'] = df.loc[x,'dp']
        df.loc[x,'dp-'] = 0
    else:
        df.loc[x,'dp-'] = 0-df.loc[x,'dp']
        df.loc[x,'dp+'] = 0

In [4]:
# add user defined loads
user_loads = {'modem':10,'rPi':4}
baseload = 0
for user_load in user_loads:
    df.loc[:,user_load]  = user_loads[user_load]
    baseload = baseload + user_loads[user_load]
#     df.loc[:,] = np.array([df['demand'].min()] * len(df))


In [5]:
# find baseload and determine remaining unkwown profile
df.loc[:,'baseload'] = np.array([df['demand'].min()-baseload] * len(df))
df.loc[:,'unknown'] = df.loc[:,'demand'] - df.loc[:,'baseload']-baseload


In [ ]:
# df[pd.isnull(df).any(axis=1)]

In [6]:
def left_round(number,precision=2):
    rem = number

    d = len(str(number))
    while(round(rem,d) == round(number,d)):
        rem = round(number,d-precision)
        d = d -1
        
    i = 0
    while(rem > 10**precision):
        rem = round(rem / 10,0)
        i = i +1
#         print(rem*(10**i))
        if i > 100:
            break
    return rem*(10**i)

left_round(00.00034564,3)

left_round(122431234.00034564,3)

# left_round(123456)

122000000.0

In [7]:
#find square loads
loads = dict()

for x in range(1,len(df)):
    #filter for dP+ with minimim power
    if df.loc[x,'dp+'] > 100:
        print(' ') #new line in output
        print ('start dp>100:',df.loc[x,'datetime'],'start P:',df.loc[x-1,'unknown'],'dP+:' ,df.loc[x,'dp+'])
        
        #look forwar in time to see how long load remains on
        for y in range(x+1,len(df)):
            #find dP- of same/simulair size 
            if df.loc[y,'dp-'] > 0.9 *df.loc[x,'dp+'] and df.loc[y,'dp-'] < 1.1 *df.loc[x,'dp+']:
                print ('stop dP-:',df.loc[y,'datetime'],'dP-:' ,df.loc[y,'dp-'])
                break
            # check if does not drop below start power (this means is must have been turned of)    
            if df.loc[y,'unknown'] <= df.loc[x-1,'unknown']:
                print ('stop demand:',df.loc[x,'datetime'] ,df.loc[y,'unknown'], ' <= ',df.loc[x-1,'unknown'])
                break
        
        print(x,y,(df.loc[x:y-1,'unknown']-df.loc[x-1,'unknown']).mean())
        
        # calculate key parameters
        mean = (df.loc[x:y-1,'unknown']-df.loc[x-1,'unknown']).mean()
        max = (df.loc[x:y-1,'unknown']-df.loc[x-1,'unknown']).max()
        min = (df.loc[x:y-1,'unknown']-df.loc[x-1,'unknown']).min()
        std = (df.loc[x:y-1,'unknown']-df.loc[x-1,'unknown']).std()
        time = pd.Timedelta(pd.to_datetime(df['datetime'][y])-pd.to_datetime(df['datetime'][x]))
        noise = df.loc[x:y-1,'dp'].abs().mean()
        
        print('mean load:',mean)
        print('max load:',max)
        print('std load:',std)
        print('noise:',noise)
        print('time past:',time)


        print('found profile from ',df.loc[x-1,'datetime'],'to',df.loc[y,'datetime'])
        profile = list(df.loc[x-1:y,'unknown']-df.loc[x-1,'unknown'])
        print(profile)
        
        
#         plt.plot(range(x,y),profile)
#         plt.title('A simple chirp')
#         plt.show()
#         break
        try:
            #drop loads which do not have a square looking profile.
            if (std/mean > 0.1):
                print('dropped because of large std:',std/mean)
                continue

            #drop loads which do not have odd start compared to mean
            if( abs(mean-df.loc[x,'dp+'])/df.loc[x,'dp+'] > 0.2):    
                print('dropped because large difference between mean and start dp+:',abs(mean-df.loc[x,'dp+'])/df.loc[x,'dp+'])
                continue
        except:
            print('Something went wrong in analysing found load, dropping ....')
            continue
#         print('hist:',df.hist(bins=10))
        
        # save this load to the distionairy (group by 'fingerprint')
        fingerprint = str(int(round(mean,-2)))+'_'#+str(int(left_round(df.loc[x,'dp+'],2)))
        temp = {'index':{'start':x,'stop':y},'time':time,'mean':mean,'max':max,'profile':profile}
        try:
            loads[fingerprint][len(loads[fingerprint])] = temp
        except:
            loads[fingerprint] = {0:temp}
            df[fingerprint] = 0 #add new colum to the dataframe before inserting found loads (only on first occurance!)
        
        df.loc[x:y-1,fingerprint] = profile[1:-1]
        df.loc[x:y-1,'unknown'] = df.loc[x:y-1,'unknown'] - profile[1:-1]
        print('Saved with fingerprint:',fingerprint)



 
start dp>100: 2017-12-14 22:40:08 start P: 103.0 dP+: 103.0
stop demand: 2017-12-14 22:40:08 102.0  <=  103.0
1819 1933 74.16666666666667
mean load: 74.16666666666667
max load: 105.0
std load: 6.445025064543645
noise: 1.4385964912280702
time past: 0 days 00:10:27
found profile from  2017-12-14 22:39:58 to 2017-12-14 22:50:35
[0.0, 103.0, 103.0, 105.0, 105.0, 103.0, 77.0, 75.0, 75.0, 73.0, 73.0, 71.0, 71.0, 71.0, 71.0, 72.0, 72.0, 72.0, 72.0, 73.0, 73.0, 73.0, 73.0, 74.0, 74.0, 74.0, 75.0, 74.0, 74.0, 74.0, 74.0, 74.0, 74.0, 74.0, 74.0, 74.0, 74.0, 74.0, 74.0, 73.0, 73.0, 74.0, 74.0, 73.0, 73.0, 73.0, 73.0, 73.0, 73.0, 73.0, 73.0, 73.0, 73.0, 72.0, 72.0, 73.0, 73.0, 73.0, 73.0, 73.0, 73.0, 72.0, 72.0, 73.0, 73.0, 73.0, 72.0, 73.0, 73.0, 73.0, 73.0, 72.0, 72.0, 73.0, 73.0, 73.0, 73.0, 72.0, 72.0, 73.0, 73.0, 72.0, 72.0, 73.0, 73.0, 72.0, 73.0, 72.0, 72.0, 72.0, 72.0, 72.0, 72.0, 72.0, 72.0, 73.0, 73.0, 73.0, 73.0, 72.0, 72.0, 72.0, 72.0, 72.0, 72.0, 72.0, 72.0, 72.0, 72.0, 72.0, 72.0, 

noise: 274.7142857142857
time past: 0 days 00:00:34
found profile from  2017-12-15 08:10:08 to 2017-12-15 08:10:52
[0.0, 1097.0, 1097.0, 1120.0, 1120.0, 1117.0, 1117.0, 317.0, -206.0]
dropped because of large std: 0.30104840406629246
 
start dp>100: 2017-12-15 08:11:02 start P: 228.0 dP+: 1277.0
stop dP-: 2017-12-15 08:11:57 dP-: 1290.0
8039 8049 1257.2
mean load: 1257.2
max load: 1278.0
std load: 26.02904360730742
noise: 133.5
time past: 0 days 00:00:55
found profile from  2017-12-15 08:10:52 to 2017-12-15 08:11:57
[0.0, 1277.0, 1277.0, 1278.0, 1278.0, 1277.0, 1277.0, 1225.0, 1225.0, 1229.0, 1229.0, -61.0]
Saved with fingerprint: 1300_
 
start dp>100: 2017-12-15 08:12:42 start P: 194.0 dP+: 158.0
stop dP-: 2017-12-15 08:12:52 dP-: 158.0
8058 8059 158.0
mean load: 158.0
max load: 158.0
std load: nan
noise: 158.0
time past: 0 days 00:00:10
found profile from  2017-12-15 08:12:41 to 2017-12-15 08:12:52
[0.0, 158.0, 0.0]
Saved with fingerprint: 200_
 
start dp>100: 2017-12-15 08:13:47 sta

Saved with fingerprint: 400_
 
start dp>100: 2017-12-15 12:48:24 start P: 0.0 dP+: 657.0
stop demand: 2017-12-15 12:48:24 0.0  <=  0.0
11027 11031 581.5
mean load: 581.5
max load: 657.0
std load: 87.17989064763348
noise: 202.0
time past: 0 days 00:00:22
found profile from  2017-12-15 12:48:19 to 2017-12-15 12:48:46
[0.0, 657.0, 657.0, 506.0, 506.0, 0.0]
dropped because of large std: 0.1499224258772717
 
start dp>100: 2017-12-15 12:49:25 start P: 0.0 dP+: 383.0
stop dP-: 2017-12-15 12:49:36 dP-: 383.0
11038 11040 383.0
mean load: 383.0
max load: 383.0
std load: 0.0
noise: 191.5
time past: 0 days 00:00:11
found profile from  2017-12-15 12:49:19 to 2017-12-15 12:49:36
[0.0, 383.0, 383.0, 0.0]
Saved with fingerprint: 400_
 
start dp>100: 2017-12-15 13:13:04 start P: 89.0 dP+: 101.0
stop demand: 2017-12-15 13:13:04 48.0  <=  89.0
11289 11532 83.58024691358025
mean load: 83.58024691358025
max load: 191.0
std load: 37.94674308399315
noise: 4.288065843621399
time past: 0 days 00:22:33
found pr

 
start dp>100: 2017-12-15 15:40:44 start P: 519.0 dP+: 112.0
stop dP-: 2017-12-15 15:41:17 dP-: 109.0
12888 12894 138.33333333333334
mean load: 138.33333333333334
max load: 167.0
std load: 24.663062799795703
noise: 33.0
time past: 0 days 00:00:33
found profile from  2017-12-15 15:40:39 to 2017-12-15 15:41:17
[0.0, 112.0, 112.0, 167.0, 167.0, 136.0, 136.0, 27.0]
dropped because of large std: 0.17828720096237857
 
start dp>100: 2017-12-15 15:42:34 start P: 479.0 dP+: 111.0
stop dP-: 2017-12-15 15:45:03 dP-: 100.0
12908 12935 1521.7777777777778
mean load: 1521.7777777777778
max load: 2103.0
std load: 814.6411354008461
noise: 119.48148148148148
time past: 0 days 00:02:29
found profile from  2017-12-15 15:42:29 to 2017-12-15 15:45:03
[0.0, 111.0, 111.0, 224.0, 224.0, 223.0, 223.0, 131.0, 1896.0, 1896.0, 2080.0, 2080.0, 1794.0, 1794.0, 1955.0, 1955.0, 2044.0, 2044.0, 2103.0, 2087.0, 2087.0, 1917.0, 1917.0, 2022.0, 2022.0, 2061.0, 2061.0, 2026.0, 1926.0]
dropped because of large std: 0.53532

13014 13019 170.6
mean load: 170.6
max load: 188.0
std load: 37.79285646785646
noise: 37.8
time past: 0 days 00:00:28
found profile from  2017-12-15 15:52:12 to 2017-12-15 15:52:45
[0.0, 103.0, 188.0, 188.0, 187.0, 187.0, 84.0]
dropped because of large std: 0.22152905315273425
 
start dp>100: 2017-12-15 15:53:07 start P: 551.0 dP+: 216.0
stop demand: 2017-12-15 15:53:07 469.0  <=  551.0
13023 13030 165.42857142857142
mean load: 165.42857142857142
max load: 216.0
std load: 55.23844416966968
noise: 61.857142857142854
time past: 0 days 00:00:38
found profile from  2017-12-15 15:53:01 to 2017-12-15 15:53:45
[0.0, 216.0, 216.0, 196.0, 88.0, 88.0, 177.0, 177.0, -82.0]
dropped because of large std: 0.33391114783047304
 
start dp>100: 2017-12-15 15:54:07 start P: 511.0 dP+: 112.0
stop dP-: 2017-12-15 15:54:57 dP-: 116.0
13034 13043 180.22222222222223
mean load: 180.22222222222223
max load: 257.0
std load: 66.97532713204501
noise: 47.111111111111114
time past: 0 days 00:00:50
found profile from

...

found profile from  2017-12-19 15:38:05 to 2017-12-19 15:38:16
[0.0, 0.0, 0.0]
Something went wrong in analysing found load, dropping ....
 
start dp>100: 2017-12-19 15:39:00 start P: 273.0 dP+: 118.0
stop demand: 2017-12-19 15:39:00 273.0  <=  273.0
75700 75701 0.0
mean load: 0.0
max load: 0.0
std load: nan
noise: 118.0
time past: 0 days 00:00:06
found profile from  2017-12-19 15:38:55 to 2017-12-19 15:39:06
[0.0, 0.0, 0.0]
Something went wrong in analysing found load, dropping ....
 
start dp>100: 2017-12-19 15:39:33 start P: 273.0 dP+: 103.0
stop demand: 2017-12-19 15:39:33 273.0  <=  273.0
75706 75707 0.0
mean load: 0.0
max load: 0.0
std load: nan
noise: 103.0
time past: 0 days 00:00:06
found profile from  2017-12-19 15:39:28 to 2017-12-19 15:39:39
[0.0, 0.0, 0.0]
Something went wrong in analysing found load, dropping ....
 
start dp>100: 2017-12-19 15:40:23 start P: 273.0 dP+: 110.0
stop demand: 2017-12-19 15:40:23 273.0  <=  273.0
75715 75716 0.0
mean load: 0.0
max load: 0.0
std 

Saved with fingerprint: 200_
 
start dp>100: 2017-12-19 16:13:45 start P: 563.0 dP+: 205.0
stop demand: 2017-12-19 16:13:45 502.0  <=  563.0
76079 76082 209.0
mean load: 209.0
max load: 211.0
std load: 3.4641016151377544
noise: 70.33333333333333
time past: 0 days 00:00:16
found profile from  2017-12-19 16:13:39 to 2017-12-19 16:14:01
[0.0, 205.0, 211.0, 211.0, -61.0]
Saved with fingerprint: 200_
 
start dp>100: 2017-12-19 16:14:12 start P: 502.0 dP+: 171.0
stop dP-: 2017-12-19 16:14:34 dP-: 178.0
76084 76088 174.0
mean load: 174.0
max load: 177.0
std load: 3.4641016151377544
noise: 44.25
time past: 0 days 00:00:22
found profile from  2017-12-19 16:14:07 to 2017-12-19 16:14:34
[0.0, 171.0, 171.0, 177.0, 177.0, -1.0]
Saved with fingerprint: 200_
 
start dp>100: 2017-12-19 16:14:40 start P: 501.0 dP+: 185.0
stop demand: 2017-12-19 16:14:40 501.0  <=  501.0
76089 76099 139.8
mean load: 139.8
max load: 185.0
std load: 68.03724470219724
noise: 35.5
time past: 0 days 00:00:55
found profile fr

time past: 0 days 00:03:40
found profile from  2017-12-19 16:42:38 to 2017-12-19 16:46:24
[0.0, 146.0, 146.0, 149.0, 149.0, 148.0, 155.0, 155.0, 156.0, 156.0, 155.0, 155.0, 152.0, 152.0, 150.0, 138.0, 138.0, 139.0, 139.0, 138.0, 138.0, 123.0, 123.0, 71.0, 71.0, 78.0, 76.0, 76.0, 79.0, 79.0, 72.0, 72.0, 69.0, 69.0, 73.0, 69.0, 69.0, 66.0, 66.0, 77.0, 77.0, -79.0]
dropped because of large std: 0.3323166812365768
 
start dp>100: 2017-12-19 17:00:42 start P: 1216.0 dP+: 126.0
stop dP-: 2017-12-19 17:01:26 dP-: 126.0
76591 76599 277.0
mean load: 277.0
max load: 369.0
std load: 107.33924857997789
noise: 46.125
time past: 0 days 00:00:44
found profile from  2017-12-19 17:00:36 to 2017-12-19 17:01:26
[0.0, 126.0, 126.0, 246.0, 246.0, 367.0, 367.0, 369.0, 369.0, 243.0]
dropped because of large std: 0.3875063125630971
 
start dp>100: 2017-12-19 17:00:53 start P: 1342.0 dP+: 120.0
stop dP-: 2017-12-19 17:01:26 dP-: 126.0
76593 76599 201.33333333333334
mean load: 201.33333333333334
max load: 243.0

[0.0, 2114.0, 2118.0, 2118.0, 2114.0, 2114.0, 2112.0, 2112.0, 2111.0, 2111.0, 2107.0, 2107.0, 2104.0, 2103.0, 2103.0, 2100.0, 2100.0, 2098.0, 2098.0, 2097.0, 2097.0, 2095.0, 2043.0, 2043.0, 2065.0, 2065.0, 2071.0, 2071.0, 2067.0, 2067.0, 2067.0, 2067.0, 2064.0, 2062.0, 2062.0, 2061.0, 2061.0, 2059.0, 2059.0, 2056.0, 2056.0, 2056.0, 2053.0, 2053.0, 2050.0, 2050.0, 2027.0, 2027.0, 2071.0, 2071.0, 2022.0, 2022.0, 2016.0, 2012.0, 2012.0, 2010.0, 2010.0, 2007.0, 2007.0, 2004.0, 2004.0, 2005.0, 2001.0, 2001.0, 2000.0, 2000.0, 2001.0, 2001.0, -19.0]
Saved with fingerprint: 2100_
 
start dp>100: 2017-12-20 00:57:11 start P: 180.0 dP+: 2061.0
stop dP-: 2017-12-20 01:09:11 dP-: 1928.0
81789 81920 1959.3358778625955
mean load: 1959.3358778625955
max load: 2064.0
std load: 70.50353081033194
noise: 17.557251908396946
time past: 0 days 00:12:00
found profile from  2017-12-20 00:57:05 to 2017-12-20 01:09:11
[0.0, 2061.0, 2061.0, 2064.0, 2064.0, 2062.0, 2062.0, 2058.0, 2058.0, 2054.0, 2054.0, 2052.0, 

std load: nan
noise: 141.0
time past: 0 days 00:00:05
found profile from  2017-12-20 06:37:50 to 2017-12-20 06:38:01
[0.0, 0.0, 0.0]
Something went wrong in analysing found load, dropping ....
 
start dp>100: 2017-12-20 06:39:13 start P: 256.0 dP+: 133.0
stop demand: 2017-12-20 06:39:13 256.0  <=  256.0
85519 85520 0.0
mean load: 0.0
max load: 0.0
std load: nan
noise: 133.0
time past: 0 days 00:00:05
found profile from  2017-12-20 06:39:07 to 2017-12-20 06:39:18
[0.0, 0.0, 0.0]
Something went wrong in analysing found load, dropping ....
 
start dp>100: 2017-12-20 06:40:35 start P: 256.0 dP+: 148.0
stop demand: 2017-12-20 06:40:35 256.0  <=  256.0
85534 85535 0.0
mean load: 0.0
max load: 0.0
std load: nan
noise: 148.0
time past: 0 days 00:00:06
found profile from  2017-12-20 06:40:30 to 2017-12-20 06:40:41
[0.0, 0.0, 0.0]
Something went wrong in analysing found load, dropping ....
 
start dp>100: 2017-12-20 06:41:58 start P: 256.0 dP+: 133.0
stop demand: 2017-12-20 06:41:58 256.0  <=  2

In [8]:
import plotly.offline
import plotly.graph_objs as go
import cufflinks
cufflinks.go_offline()

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [9]:
start = 0
points = 1000
try:
    start = plots * points
except:
    plots = 0
# plots = 0

    
res = df.set_index('datetime')
res[start:start+points].iplot(kind='line')

plots = plots +1
# df[].iplot()

In [10]:
# print(list(loads['100_'][0]))
for i in sorted(loads):
    print(i,'has',len(loads[i]),'occurance(s)')
#     for load in loads[i]:
#         if i == '100_':
#             print(round(sum(loads[i][load]['profile'])/360,1),'Wh in ',loads[i][load]['time'])
            


1000_ has 5 occurance(s)
100_ has 55 occurance(s)
1100_ has 13 occurance(s)
1200_ has 4 occurance(s)
1300_ has 7 occurance(s)
1400_ has 2 occurance(s)
1600_ has 1 occurance(s)
1700_ has 1 occurance(s)
1800_ has 6 occurance(s)
1900_ has 9 occurance(s)
2000_ has 23 occurance(s)
200_ has 38 occurance(s)
2100_ has 10 occurance(s)
2200_ has 5 occurance(s)
2400_ has 1 occurance(s)
300_ has 6 occurance(s)
400_ has 4 occurance(s)
500_ has 6 occurance(s)
600_ has 5 occurance(s)
700_ has 21 occurance(s)
800_ has 7 occurance(s)
900_ has 3 occurance(s)


In [11]:

res = df.set_index('datetime')
# res[:1000].iplot(kind='line')
# fig = res.plot()
# fig.show()
res.resample('10T').iplot(kind='line')



# res[:100]

/Applications/anaconda/lib/python3.6/site-packages/ipykernel_launcher.py:6: FutureWarning:


.resample() is now a deferred operation
You called iplot(...) on this deferred object which materialized it into a dataframe
by implicitly taking the mean.  Use .resample(...).mean() instead



In [12]:

# df[['datetime',list(loads)]].iplot()
temp = list(loads)
temp[0] = 'datetime'
temp[1] = 'baseload'
temp[2] = 'unknown'

temp[3:] =list(loads)
dp = df[temp]
dp = dp.set_index('datetime')
dp.resample('10T').mean().iplot(kind='line')
# dp.resample('10T').mean().iplot(kind='area',fill='tozeroy',mode='none')



In [13]:
pie = dp.sum()
# values = pie.values/pie.sum()*100
round(pie/pie.sum()*100,1)


baseload    -4.2
unknown     65.8
2100_        7.2
2200_        3.5
2000_       14.1
1100_        0.4
600_         0.2
200_         0.1
800_         0.6
700_         1.1
1300_        0.2
1000_        0.1
500_         0.0
1800_        1.3
400_         0.0
100_         0.1
1900_        8.3
900_         0.0
1200_        0.0
1400_        0.1
300_         0.0
1600_        0.0
2400_        0.7
1700_        0.4
dtype: float64

In [14]:
trace = go.Pie(labels=pie.index, values=pie.values)
dp.iplot([trace], filename=name)

In [15]:
# import plotly.plotly as py
import plotly.offline as py

trace = go.Pie(labels=pie.index, values=pie.values)

py.plot([trace], filename='disaggregator_results_pie.html')

'file:///Users/arnekaas/Documents/GitHub/disaggregation/disaggregator-deltaPower/disaggregator_results_pie.html'

# Try to rename colums for 'kwown loads' 

In [16]:
#relable output for known_loads
known_loads = {'100_':'Fridge','2000_':'Iron'}
for name in loads.keys():
    try:
        df=df.rename(columns = {name:known_loads[name]})
        loads[known_loads[name]] = loads[name]
    except:
        print(name,'not found known_loads')
    
for name in known_loads:
    try:
        del loads[name]
    except:
        print(name,'not found in legend')

legend = loads.keys()
print(list(legend))

2100_ not found known_loads
2200_ not found known_loads


RuntimeError: dictionary changed size during iteration